# Training and inference of ALIGNN models for IDAO-22
Team: NESCafe Gold 3in1

**ALL THE TRAINING AND INFERENCE WAS ON GOOGLE COLAB WITH TESLAS V100/A100**


## If you have a Tesla A100 rolled

In case you have A100, I think this should work (not tested yet)

In [ ]:
!apt-get --purge remove cuda nvidia* libnvidia-*
!dpkg -l | grep cuda- | awk '{print $2}' | xargs -n1 dpkg --purge
!apt-get remove cuda-*
!apt autoremove
!apt-get update

In [ ]:
!wget https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64/cuda-ubuntu1804.pin
!mv cuda-ubuntu1804.pin /etc/apt/preferences.d/cuda-repository-pin-600
!wget https://developer.download.nvidia.com/compute/cuda/11.3.0/local_installers/cuda-repo-ubuntu1804-11-3-local_11.3.0-465.19.01-1_amd64.deb
!dpkg -i cuda-repo-ubuntu1804-11-3-local_11.3.0-465.19.01-1_amd64.deb
!apt-key add /var/cuda-repo-ubuntu1804-11-3-local/7fa2af80.pub
!apt-get update
!apt-get -y install cuda

## Google Drive connectors, datasets downloaders

In [ ]:
from google.colab import drive
import os

# drive.mount('/content/drive')
%cd /content/drive/MyDrive/Colab\ Notebooks/Competitions/IDAO/
os.environ['KAGGLE_CONFIG_DIR'] = "/content/drive/MyDrive/Colab Notebooks/Competitions/"

/content/drive/MyDrive/Colab Notebooks/Competitions/IDAO


In [ ]:
!kaggle datasets download yk4r22/idao-22

100% 102M/102M [00:01<00:00, 95.4MB/s] 
100% 102M/102M [00:01<00:00, 61.3MB/s]


In [ ]:
!unzip idao-22.zip

In [ ]:
!mkdir -p datasets
!mv data/* datasets/
!rm -r data

## Pip installs
Don't forget to restart runtime while on Google Colab

In [ ]:
import os
# Clone ALIGNN repo to get example folder
if not os.path.exists('alignn'):
    !git clone https://github.com/yk4r2/alignn.git
else:
    !cd alignn && git fetch && git pull

!pip install jarvis-tools alignn/ dgl-cu111 --upgrade
!pip install pymatgen==2020.11.11

## Fine-tuning


In [ ]:
!find models/*.zip -exec unzip {} \;
!mv models/trained/* models/ && rm -rf models/trained

### Models reading

In [ ]:
from alignn.models.alignn import ALIGNN
import torch

device = torch.device('cuda')

jv_mbj_bandgap_alignn = ALIGNN()
jv_mbj_bandgap_alignn.load_state_dict(torch.load('models/jv_mbj_bandgap_alignn/checkpoint_70.pt')["model"])
jv_mbj_bandgap_alignn.to(device)
# jv_mbj_bandgap_alignn.eval()

mp_gappbe_alignnn = ALIGNN()
mp_gappbe_alignnn.load_state_dict(torch.load('models/mp_gappbe_alignnn/checkpoint_95.pt')["model"])
mp_gappbe_alignnn.to(device)
# mp_gappbe_alignnn.eval()

ALIGNN(
  (atom_embedding): MLPLayer(
    (layer): Sequential(
      (0): Linear(in_features=92, out_features=256, bias=True)
      (1): BatchNorm1d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): SiLU()
    )
  )
  (edge_embedding): Sequential(
    (0): RBFExpansion()
    (1): MLPLayer(
      (layer): Sequential(
        (0): Linear(in_features=80, out_features=64, bias=True)
        (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (2): SiLU()
      )
    )
    (2): MLPLayer(
      (layer): Sequential(
        (0): Linear(in_features=64, out_features=256, bias=True)
        (1): BatchNorm1d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (2): SiLU()
      )
    )
  )
  (angle_embedding): Sequential(
    (0): RBFExpansion()
    (1): MLPLayer(
      (layer): Sequential(
        (0): Linear(in_features=40, out_features=64, bias=True)
        (1): BatchNorm1d(64, eps=1e-05, momentum=0.

Layers freeze code

In [ ]:
from alignn.train_folder import train_for_folder

def freeze(
    model,
    freeze_edge_emb=False,
    freeze_angle_emb=False,
    freeze_bn=True,
    freeze_src=True,
    freeze_dst=True,
    freeze_edge_gate=True,
    freeze_other=False,
):
    for name, p in model.named_parameters():
        name = name.lower()
        if 'bn' in name or 'norm' in name:
            p.requires_grad = not freeze_bn
        elif 'angle_embedding' in name:
            p.requires_grad = not freeze_angle_emb
        elif 'edge_embedding' in name:
            p.requires_grad = not freeze_edge_emb
        elif 'src' in name:
            p.requires_grad = not freeze_src
        elif 'dst' in name:
            p.requires_grad = not freeze_dst
        elif 'edge_gate' in name:
            p.requires_grad = not freeze_edge_gate
        else:
            p.requires_grad = not freeze_other
    return model

In case you downloaded data from Kaggle in zip-extensions

In [ ]:
!unzip datasets/data.zip
!mv eval datasets
!mv train datasets

### Training
### ❗️ If you want to train ALIGNNs on no_defects (original) data ❗️
CHANGE PLEASE `datasets/train/defects/jarvis` TO `datasets/train/no_defects/jarvis` AND UNCOMMENT ONE OF TWO FREEZE POSSIBILITIES

In [ ]:
# %%time
# jv_mbj_bandgap_alignn = freeze(
#     jv_mbj_bandgap_alignn,
#     freeze_edge_emb=True,
#     freeze_angle_emb=True,
#     freeze_bn=False,
#     freeze_src=False,
#     freeze_dst=False,
#     freeze_edge_gate=False,
#     freeze_other=False,
# )
# jv_mbj_bandgap_alignn = freeze(jv_mbj_bandgap_alignn)
train_for_folder(
    root_dir='datasets/train/defects/jarvis',
    model=jv_mbj_bandgap_alignn,
    batch_size=32,
    config_name='models/jv_mbj_bandgap_alignn/config.json',
    output_dir='models/trained/jv_mbj_bandgap_alignn_defects',
    )

MAX val: 1.8106
MIN val: 0.0938999999999999
MAD: 0.4596230686826515
Baseline MAE: 0.45039721269541044
data range 1.8106 0.1720999999999999
building line graphs



100%|██████████| 2372/2372 [00:01<00:00, 1658.91it/s]


data range 1.8103 0.2542
building line graphs



100%|██████████| 2372/2372 [00:01<00:00, 1579.64it/s]


data range 1.8103 0.0938999999999999
building line graphs


...

[1/74]   1%|1          [00:00<?]

Val_MAE: 0.5513
Train_MAE: 0.0027


[1/74]   1%|1          [00:00<?]

2022-03-13 23:50:27,665 ignite.handlers.early_stopping.EarlyStopping INFO: EarlyStopping: Stop training


Val_MAE: 0.5517
Train_MAE: 0.0019
Test MAE: 0.5756928769720567
Time taken (s): 1757.996512889862


In [ ]:
 !zip -r 'cache/dft_3d-k-nearest.zip' 'cache/dft_3d-k-nearest.bin'

  adding: cache/dft_3d-k-nearest.bin (deflated 93%)


In [ ]:
!zip -r 'models/trained/jv_mbj_bandgap_alignn_defects/jv_mbj_bandgap_alignn_defects.zip' 'models/trained/jv_mbj_bandgap_alignn_defects/'

  adding: models/trained/jv_mbj_bandgap_alignn_defects/ (stored 0%)
  adding: models/trained/jv_mbj_bandgap_alignn_defects/ids_train_val_test.json (deflated 81%)
  adding: models/trained/jv_mbj_bandgap_alignn_defects/mad (deflated 23%)
  adding: models/trained/jv_mbj_bandgap_alignn_defects/train_data_data_range (deflated 24%)
  adding: models/trained/jv_mbj_bandgap_alignn_defects/val_data_data_range (stored 0%)
  adding: models/trained/jv_mbj_bandgap_alignn_defects/test_data_data_range (deflated 24%)
  adding: models/trained/jv_mbj_bandgap_alignn_defects/config.json (deflated 58%)
  adding: models/trained/jv_mbj_bandgap_alignn_defects/history_val.json (deflated 78%)
  adding: models/trained/jv_mbj_bandgap_alignn_defects/history_train.json (deflated 77%)
  adding: models/trained/jv_mbj_bandgap_alignn_defects/checkpoint_176.pt (deflated 8%)
  adding: models/trained/jv_mbj_bandgap_alignn_defects/checkpoint_177.pt (deflated 7%)
  adding: models/trained/jv_mbj_bandgap_alignn_defects/predict

**❗️ If you want to train ALIGNNs on no_defects (original) data ❗️**

CHANGE PLEASE `datasets/train/defects/jarvis` TO `datasets/train/no_defects/jarvis` AND UNCOMMENT ONE OF TWO FREEZE POSSIBILITIES

In [ ]:
}%%time
# fr_mp_gappbe_alignnn = freeze(
    # mp_gappbe_alignnn,
    # freeze_edge_emb=True,
    # freeze_angle_emb=True,
    # freeze_bn=False,
    # freeze_src=False,
    # freeze_dst=False,
    # freeze_edge_gate=False,
    # freeze_other=False,
# )
train_for_folder(
    root_dir='datasets/train/defects/jarvis',
    model=mp_gappbe_alignnn,
    batch_size=32,
    config_name='models/mp_gappbe_alignnn/config.json',
    output_dir='models/trained/mp_gappbe_alignnn_defects',
    )

MAX val: 1.8106
MIN val: 0.0938999999999999
MAD: 0.4596230686826515
Baseline MAE: 0.45039721269541044
data range 1.8106 0.1720999999999999
building line graphs



100%|██████████| 2372/2372 [00:01<00:00, 1608.59it/s]


data range 1.8103 0.2542
building line graphs



100%|██████████| 2372/2372 [00:01<00:00, 1601.89it/s]


data range 1.8103 0.0938999999999999
building line graphs


...

[1/74]   1%|1          [00:00<?]

Val_MAE: 0.5504
Train_MAE: 0.0038


[1/74]   1%|1          [00:00<?]

2022-03-14 00:27:52,252 ignite.handlers.early_stopping.EarlyStopping INFO: EarlyStopping: Stop training


Val_MAE: 0.5506
Train_MAE: 0.0039
Test MAE: 0.5740989764296526
Time taken (s): 1510.7254157066345
CPU times: user 22min 19s, sys: 2min 14s, total: 24min 33s
Wall time: 25min 21s


In [ ]:
!zip -r 'models/trained/mp_gappbe_alignnn_defects/mp_gappbe_alignnn_defects.zip' 'models/trained/mp_gappbe_alignnn_defects/'

  adding: models/trained/mp_gappbe_alignnn_defects/ (stored 0%)
  adding: models/trained/mp_gappbe_alignnn_defects/ids_train_val_test.json (deflated 81%)
  adding: models/trained/mp_gappbe_alignnn_defects/mad (deflated 23%)
  adding: models/trained/mp_gappbe_alignnn_defects/train_data_data_range (deflated 24%)
  adding: models/trained/mp_gappbe_alignnn_defects/val_data_data_range (stored 0%)
  adding: models/trained/mp_gappbe_alignnn_defects/test_data_data_range (deflated 24%)
  adding: models/trained/mp_gappbe_alignnn_defects/config.json (deflated 59%)
  adding: models/trained/mp_gappbe_alignnn_defects/history_val.json (deflated 78%)
  adding: models/trained/mp_gappbe_alignnn_defects/history_train.json (deflated 77%)
  adding: models/trained/mp_gappbe_alignnn_defects/checkpoint_150.pt (deflated 8%)
  adding: models/trained/mp_gappbe_alignnn_defects/checkpoint_151.pt (deflated 8%)
  adding: models/trained/mp_gappbe_alignnn_defects/prediction_results_test_set.csv (deflated 71%)
  adding

In [ ]:
jv_optb88vdw_bandgap_alignn = ALIGNN()
jv_optb88vdw_bandgap_alignn.load_state_dict(torch.load('models/jv_optb88vdw_bandgap_alignn/checkpoint_52.pt')["model"])
# jv_optb88vdw_bandgap_alignn.half()
jv_optb88vdw_bandgap_alignn.to(device)
# jv_optb88vdw_bandgap_alignn.eval()


qm9_gap_alignn = ALIGNN()
qm9_gap_alignn.load_state_dict(torch.load('models/qm9_gap_alignn/checkpoint_60.pt')["model"])
# qm9_gap_alignn.half()
qm9_gap_alignn.to(device)
# qm9_gap_alignn.eval()

ALIGNN(
  (atom_embedding): MLPLayer(
    (layer): Sequential(
      (0): Linear(in_features=92, out_features=256, bias=True)
      (1): BatchNorm1d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): SiLU()
    )
  )
  (edge_embedding): Sequential(
    (0): RBFExpansion()
    (1): MLPLayer(
      (layer): Sequential(
        (0): Linear(in_features=80, out_features=64, bias=True)
        (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (2): SiLU()
      )
    )
    (2): MLPLayer(
      (layer): Sequential(
        (0): Linear(in_features=64, out_features=256, bias=True)
        (1): BatchNorm1d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (2): SiLU()
      )
    )
  )
  (angle_embedding): Sequential(
    (0): RBFExpansion()
    (1): MLPLayer(
      (layer): Sequential(
        (0): Linear(in_features=40, out_features=64, bias=True)
        (1): BatchNorm1d(64, eps=1e-05, momentum=0.

**❗️ If you want to train ALIGNNs on no_defects (original) data ❗️**

CHANGE PLEASE `datasets/train/defects/jarvis` TO `datasets/train/no_defects/jarvis` AND UNCOMMENT ONE OF TWO FREEZE POSSIBILITIES

In [ ]:
%%time
# fr_jv_optb88vdw_bandgap_alignn = freeze(
    # jv_optb88vdw_bandgap_alignn,
    # freeze_edge_emb=True,
    # freeze_angle_emb=True,
    # freeze_bn=False,
    # freeze_src=False,
    # freeze_dst=False,
    # freeze_edge_gate=False,
    # freeze_other=False,
    # )
train_for_folder(
    root_dir='datasets/train/defects/jarvis',
    model=jv_optb88vdw_bandgap_alignn,
    batch_size=32,
    config_name='models/jv_optb88vdw_bandgap_alignn/config.json',
    output_dir='models/trained/jv_optb88vdw_bandgap_alignn_defects',
    )

MAX val: 1.8106
MIN val: 0.0938999999999999
MAD: 0.4596230686826515
Baseline MAE: 0.45039721269541044
data range 1.8106 0.1720999999999999
building line graphs



100%|██████████| 2372/2372 [00:02<00:00, 1123.76it/s]


data range 1.8103 0.2542
building line graphs



100%|██████████| 2372/2372 [00:01<00:00, 1639.37it/s]


data range 1.8103 0.0938999999999999
building line graphs


...

[1/74]   1%|1          [00:00<?]

Val_MAE: 0.5478
Train_MAE: 0.0086


[1/74]   1%|1          [00:00<?]

2022-03-14 00:53:46,675 ignite.handlers.early_stopping.EarlyStopping INFO: EarlyStopping: Stop training


Val_MAE: 0.5460
Train_MAE: 0.0140
Test MAE: 0.5696332418938747
Time taken (s): 1537.4912989139557
CPU times: user 22min 40s, sys: 2min 16s, total: 24min 57s
Wall time: 25min 48s


In [ ]:
!zip -r 'models/trained/jv_optb88vdw_bandgap_alignn_defects/jv_optb88vdw_bandgap_alignn_defects.zip' 'models/trained/jv_optb88vdw_bandgap_alignn_defects/'

  adding: models/trained/jv_optb88vdw_bandgap_alignn_defects/ (stored 0%)
  adding: models/trained/jv_optb88vdw_bandgap_alignn_defects/ids_train_val_test.json (deflated 81%)
  adding: models/trained/jv_optb88vdw_bandgap_alignn_defects/mad (deflated 23%)
  adding: models/trained/jv_optb88vdw_bandgap_alignn_defects/train_data_data_range (deflated 24%)
  adding: models/trained/jv_optb88vdw_bandgap_alignn_defects/val_data_data_range (stored 0%)
  adding: models/trained/jv_optb88vdw_bandgap_alignn_defects/test_data_data_range (deflated 24%)
  adding: models/trained/jv_optb88vdw_bandgap_alignn_defects/config.json (deflated 58%)
  adding: models/trained/jv_optb88vdw_bandgap_alignn_defects/history_val.json (deflated 77%)
  adding: models/trained/jv_optb88vdw_bandgap_alignn_defects/history_train.json (deflated 76%)
  adding: models/trained/jv_optb88vdw_bandgap_alignn_defects/checkpoint_154.pt (deflated 7%)
  adding: models/trained/jv_optb88vdw_bandgap_alignn_defects/checkpoint_155.pt (deflated 

**❗️ If you want to train ALIGNNs on no_defects (original) data ❗️**

CHANGE PLEASE `datasets/train/defects/jarvis` TO `datasets/train/no_defects/jarvis` AND UNCOMMENT ONE OF TWO FREEZE POSSIBILITIES

In [ ]:
%%time
# fr_qm9_gap_alignn = freeze(
    # qm9_gap_alignn,
    # freeze_edge_emb=True,
    # freeze_angle_emb=True,
    # freeze_bn=False,
    # freeze_src=False,
    # freeze_dst=False,
    # freeze_edge_gate=False,
    # freeze_other=False,
    # )
train_for_folder(
    root_dir='datasets/train/defects/jarvis',
    model=qm9_gap_alignn,
    batch_size=8,
    config_name='models/qm9_gap_alignn/config.json',
    output_dir='models/trained/qm9_gap_alignn_defects',
    )

MAX val: 1.8106
MIN val: 0.0938999999999999
MAD: 0.4596230686826515
Baseline MAE: 0.45039721269541044
data range 1.8106 0.1720999999999999
building line graphs



100%|██████████| 2372/2372 [00:01<00:00, 1681.45it/s]


data range 1.8103 0.2542
building line graphs



100%|██████████| 2372/2372 [00:01<00:00, 1569.32it/s]


data range 1.8103 0.0938999999999999
building line graphs


...

[1/296]   0%|           [00:00<?]

Val_MAE: 0.5406
Train_MAE: 0.0135


[1/296]   0%|           [00:00<?]

2022-03-14 01:50:32,332 ignite.handlers.early_stopping.EarlyStopping INFO: EarlyStopping: Stop training


Val_MAE: 0.5431
Train_MAE: 0.0125
Test MAE: 0.5724400990214702
Time taken (s): 3388.646849155426
CPU times: user 52min 42s, sys: 3min, total: 55min 43s
Wall time: 56min 39s


In [ ]:
!zip -r 'models/trained/qm9_gap_alignn_defects/qm9_gap_alignn_defects.zip' 'models/trained/qm9_gap_alignn_defects/'

  adding: models/trained/qm9_gap_alignn_defects/ (stored 0%)
  adding: models/trained/qm9_gap_alignn_defects/ids_train_val_test.json (deflated 81%)
  adding: models/trained/qm9_gap_alignn_defects/mad (deflated 23%)
  adding: models/trained/qm9_gap_alignn_defects/train_data_data_range (deflated 24%)
  adding: models/trained/qm9_gap_alignn_defects/val_data_data_range (stored 0%)
  adding: models/trained/qm9_gap_alignn_defects/test_data_data_range (deflated 24%)
  adding: models/trained/qm9_gap_alignn_defects/config.json (deflated 59%)
  adding: models/trained/qm9_gap_alignn_defects/history_val.json (deflated 77%)
  adding: models/trained/qm9_gap_alignn_defects/history_train.json (deflated 76%)
  adding: models/trained/qm9_gap_alignn_defects/checkpoint_102.pt (deflated 8%)
  adding: models/trained/qm9_gap_alignn_defects/checkpoint_103.pt (deflated 8%)
  adding: models/trained/qm9_gap_alignn_defects/prediction_results_test_set.csv (deflated 70%)
  adding: models/trained/qm9_gap_alignn_defe

## Inference

In [ ]:
!kaggle datasets download yk4r22/idao-22

Traceback (most recent call last):
  File "/usr/local/bin/kaggle", line 5, in <module>
    from kaggle.cli import main
  File "/usr/local/lib/python3.7/dist-packages/kaggle/__init__.py", line 23, in <module>
    api.authenticate()
  File "/usr/local/lib/python3.7/dist-packages/kaggle/api/kaggle_api_extended.py", line 166, in authenticate
    self.config_file, self.config_dir))
OSError: Could not find kaggle.json. Make sure it's located in /root/.kaggle. Or use the environment method.


In [ ]:
from alignn import train
from jarvis.core.atoms import Atoms
import glob
from alignn.pretrained import get_multiple_predictions as predict
from tqdm.notebook import tqdm

In [ ]:
atoms_array = []
ids_array = []
for i in tqdm(glob.glob("datasets/eval/no_defects/jarvis/*.vasp")):
    atoms = Atoms.from_poscar(i)
    id = i.split('/')[-1].split('.vasp')[0]
    atoms_array.append(atoms)
    ids_array.append(id)

  0%|          | 0/2967 [00:00<?, ?it/s]

In [ ]:
atoms_array[0]

In case you want to use pretrained models (jarvis will download them for you)

In [ ]:
# %%time
# predict(atoms_array=atoms_array,
#         idx_array=ids_array,
#         model_name='jv_optb88vdw_bandgap_alignn',
#         filename='jv_optb88vdw_bandgap_alignn_pred.json',
#         )
# predict(atoms_array=atoms_array,
#         idx_array=ids_array,
#         model_name='jv_mbj_bandgap_alignn',
#         filename='jv_mbj_bandgap_alignn_pred.json',
#         )

Using fine-tuned models

**WATCH YOUR PATHS**

In [ ]:
from alignn.models.alignn import ALIGNN
import torch

device = torch.device('cuda')

qm9_gap_alignn = ALIGNN()
qm9_gap_alignn.load_state_dict(torch.load('models/ALIGNN/defects/qm9_gap_alignn/checkpoint_60.pt')["model"])
qm9_gap_alignn.to(device)
qm9_gap_alignn.eval()

mp_gappbe_alignnn = ALIGNN()
mp_gappbe_alignnn.load_state_dict(torch.load('models/ALIGNN/defects/mp_gappbe_alignnn/checkpoint_95.pt')["model"])
mp_gappbe_alignnn.to(device)
mp_gappbe_alignnn.eval()

jv_optb88vdw_bandgap_alignn = ALIGNN()
jv_optb88vdw_bandgap_alignn.load_state_dict(torch.load('models/ALIGNN/defects/jv_optb88vdw_bandgap_alignn/checkpoint_52.pt')["model"])
jv_optb88vdw_bandgap_alignn.to(device)
jv_optb88vdw_bandgap_alignn.eval()

jv_mbj_bandgap_alignn = ALIGNN()
jv_mbj_bandgap_alignn.load_state_dict(torch.load('models/ALIGNN/defects/jv_mbj_bandgap_alignn/checkpoint_70.pt')["model"])
jv_mbj_bandgap_alignn.to(device)
jv_mbj_bandgap_alignn.eval()

ALIGNN(
  (atom_embedding): MLPLayer(
    (layer): Sequential(
      (0): Linear(in_features=92, out_features=256, bias=True)
      (1): BatchNorm1d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): SiLU()
    )
  )
  (edge_embedding): Sequential(
    (0): RBFExpansion()
    (1): MLPLayer(
      (layer): Sequential(
        (0): Linear(in_features=80, out_features=64, bias=True)
        (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (2): SiLU()
      )
    )
    (2): MLPLayer(
      (layer): Sequential(
        (0): Linear(in_features=64, out_features=256, bias=True)
        (1): BatchNorm1d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (2): SiLU()
      )
    )
  )
  (angle_embedding): Sequential(
    (0): RBFExpansion()
    (1): MLPLayer(
      (layer): Sequential(
        (0): Linear(in_features=40, out_features=64, bias=True)
        (1): BatchNorm1d(64, eps=1e-05, momentum=0.

In [ ]:
%%time
predict(atoms_array=atoms_array,
        idx_array=ids_array,
        model=qm9_gap_alignn,
        filename='qm9_gap_alignn_pred_eval_no_defects.json',
        )

predict(atoms_array=atoms_array,
        idx_array=ids_array,
        model=mp_gappbe_alignnn,
        filename='mp_gappbe_alignnn_pred_eval_no_defects.json',
        )

predict(atoms_array=atoms_array,
        idx_array=ids_array,
        model=jv_optb88vdw_bandgap_alignn,
        filename='jv_optb88vdw_bandgap_alignn_pred_eval_no_defects.json',
        )

predict(atoms_array=atoms_array,
        idx_array=ids_array,
        model=jv_mbj_bandgap_alignn,
        filename='jv_mbj_bandgap_alignn_pred_eval_no_defects.json',
        )

data range -9999 -9999
building line graphs


100%|██████████| 2967/2967 [00:01<00:00, 1636.22it/s]


100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
data range -9999 -9999
building line graphs


100%|██████████| 2967/2967 [00:01<00:00, 1687.02it/s]


100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
data range -9999 -9999
building line graphs


100%|██████████| 2967/2967 [00:01<00:00, 1671.50it/s]


100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
data range -9999 -9999
building line graphs


100%|██████████| 2967/2967 [00:01<00:00, 1669.81it/s]


100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
CPU times: user 4min 44s, sys: 1.35 s, total: 4min 45s
Wall time: 4min 44s


In [ ]:
!rm -rf *.json